https://gitlab.com/bigirqu/quranqa/-/tree/main/datasets

https://gitlab.com/bigirqu/quranqa/-/tree/main/code

In [ ]:
!pip install simpletransformers

     |████████████████████████████████| 249 kB 4.2 MB/s 
     |████████████████████████████████| 10.1 MB 65.3 MB/s 
     |████████████████████████████████| 3.8 MB 58.7 MB/s 
     |████████████████████████████████| 43 kB 2.4 MB/s 
     |████████████████████████████████| 1.2 MB 74.8 MB/s 
     |████████████████████████████████| 325 kB 94.3 MB/s 
     |████████████████████████████████| 1.7 MB 67.3 MB/s 
     |████████████████████████████████| 6.5 MB 80.1 MB/s 
     |████████████████████████████████| 895 kB 75.4 MB/s 
     |████████████████████████████████| 67 kB 6.3 MB/s 
     |████████████████████████████████| 596 kB 74.3 MB/s 
     |████████████████████████████████| 181 kB 61.5 MB/s 
     |████████████████████████████████| 144 kB 95.5 MB/s 
     |████████████████████████████████| 63 kB 2.4 MB/s 
     |████████████████████████████████| 1.1 MB 53.0 MB/s 
     |████████████████████████████████| 212 kB 93.4 MB/s 
     |████████████████████████████████| 134 kB 47.5 MB/s 
     |██████████████

In [ ]:
!git clone https://gitlab.com/bigirqu/quranqa.git

Cloning into 'quranqa'...
remote: Enumerating objects: 261, done.
remote: Counting objects: 100% (98/98), done.
remote: Compressing objects: 100% (76/76), done.
remote: Total 261 (delta 35), reused 70 (delta 22), pack-reused 163
Receiving objects: 100% (261/261), 300.16 KiB | 1.49 MiB/s, done.
Resolving deltas: 100% (89/89), done.


In [ ]:
import pandas as pd


In [ ]:
train = pd.read_json("/content/quranqa/datasets/qrcd_v1.1_train.jsonl",lines = True)

In [ ]:
test = pd.read_json("/content/quranqa/datasets/qrcd_v1.1_dev.jsonl",lines = True)

In [ ]:
train.head()

pq_id                                            passage  surah  \
0     2:8-16_364  ومن الناس من يقول آمنا بالله وباليوم الآخر وما...      2   
1  2:174-176_364  إن الذين يكتمون ما أنزل الله من الكتاب ويشترون...      2   
2   14:47-52_364  فلا تحسبن الله مخلف وعده رسله إن الله عزيز ذو ...     14   
3   17:12-17_364  وجعلنا الليل والنهار آيتين فمحونا آية الليل وج...     17   
4   18:29-31_364  وقل الحق من ربكم فمن شاء فليؤمن ومن شاء فليكفر...     18   

    verses                                           question  \
0     8-16  لماذا سيُحاسب ويُعذب الضال يوم القيامة ان كان ...   
1  174-176  لماذا سيُحاسب ويُعذب الضال يوم القيامة ان كان ...   
2    47-52  لماذا سيُحاسب ويُعذب الضال يوم القيامة ان كان ...   
3    12-17  لماذا سيُحاسب ويُعذب الضال يوم القيامة ان كان ...   
4    29-31  لماذا سيُحاسب ويُعذب الضال يوم القيامة ان كان ...   

                                             answers  
0  [{'text': 'أولئك الذين اشتروا الضلالة بالهدى',...  
1  [{'text': 'أولئك الذين اشتروا الضلالة بالهدى و...  
2  [{'text': 'ليجزي الله كل نفس ما كسبت', 'start_...  
3  [{'text': 'كل إنسان ألزمناه طائره في عنقه', 's...  
4  [{'text': 'من شاء فليؤمن ومن شاء فليكفر', 'sta...

In [ ]:
train.answers.values[0]

[{'text': 'أولئك الذين اشتروا الضلالة بالهدى', 'start_char': 504}]

In [ ]:
def chnager(s):
  returned_list = []
  for l_dict in s:
    d = {'text':l_dict['text'],'answer_start':l_dict['start_char']}
    returned_list.append(d)
  return returned_list

In [ ]:
train['answers'] = train['answers'].apply(lambda x:chnager(x))

In [ ]:
test['answers'] = test['answers'].apply(lambda x:chnager(x))

In [ ]:
final_dict_train = list()
for id, contxt,qn,answrs in zip(train.pq_id.values,train.passage.values,train.question.values,train.answers.values):
  ele_dict = dict()
  ele_dict['context'] = contxt
  l = []
  dd = {"id":id,"is_impossible": False,"question":qn,"answers":answrs}
  l.append(dd)
  ele_dict['qas'] = l
  final_dict_train.append(ele_dict)

In [ ]:
# fianl_dict

In [ ]:
final_dict_test = list()
for id, contxt,qn,answrs in zip(test.pq_id.values,test.passage.values,test.question.values,test.answers.values):
  ele_dict = dict()
  ele_dict['context'] = contxt
  l = []
  dd = {"id":id,"is_impossible": False,"question":qn,"answers":answrs}
  l.append(dd)
  ele_dict['qas'] = l
  final_dict_test.append(ele_dict)

In [ ]:
type(final_dict_test)

list

In [ ]:
import logging

from simpletransformers.question_answering import QuestionAnsweringModel, QuestionAnsweringArgs

logging.basicConfig(level=logging.INFO)
transformers_logger = logging.getLogger("transformers")
transformers_logger.setLevel(logging.WARNING)

In [ ]:
import wandb



In [ ]:
model_args = QuestionAnsweringArgs(n_best_size=8)
model_args.train_batch_size = 32
model_args.evaluate_during_training = True

In [ ]:
model_args.learning_rate= 0.000372
model_args.max_seq_length = 128


In [ ]:
# model_args.max_query_length
# model_args.max_answer_length

In [ ]:
# sweep_config = {
#     "method": "bayes",  # grid, random
#     "metric": {"name": "train_loss", "goal": "minimize"},
#     "parameters": {
#         "num_train_epochs": {"values": [5,8,10]},
#         "learning_rate": {"min": 5e-5, "max": 4e-4},
#         "train_batch_size":{"values":[8,16,32]},
#         "max_seq_length":{"values":[64,128,96]},

#     },
# }

# sweep_id = wandb.sweep(sweep_config, project="Simple Sweep")

In [ ]:
train_data = final_dict_train
eval_data = final_dict_test

In [ ]:
import pprint
pprint.pprint(model_args)

QuestionAnsweringArgs(adafactor_beta1=None, adafactor_clip_threshold=1.0, adafactor_decay_rate=-0.8, adafactor_eps=(1e-30, 0.001), adafactor_relative_step=True, adafactor_scale_parameter=True, adafactor_warmup_init=True, adam_epsilon=1e-08, best_model_dir='outputs/best_model', cache_dir='cache_dir/', config={}, cosine_schedule_num_cycles=0.5, custom_layer_parameters=[], custom_parameter_groups=[], dataloader_num_workers=0, do_lower_case=False, dynamic_quantize=False, early_stopping_consider_epochs=False, early_stopping_delta=0, early_stopping_metric='correct', early_stopping_metric_minimize=False, early_stopping_patience=3, encoding=None, eval_batch_size=8, evaluate_during_training=True, evaluate_during_training_silent=True, evaluate_during_training_steps=2000, evaluate_during_training_verbose=False, evaluate_each_epoch=True, fp16=True, gradient_accumulation_steps=1, learning_rate=0.000152, local_rank=-1, logging_steps=50, loss_type=None, loss_args={}, manual_seed=None, max_grad_norm=1

In [ ]:
model_args.num_train_epochs = 5

In [ ]:
# model_args.wandb_project = "Simple Sweep"

In [ ]:
model_args.overwrite_output_dir=True

In [ ]:
# def train():
#   wandb.init()
#   model = QuestionAnsweringModel(
#       "bert", "asafaya/bert-base-arabic", args=model_args,sweep_config=wandb.config
#   )
#   # Train the model
#   model.train_model(train_data, eval_data=eval_data,output_dir='tillu')

#   # Evaluate the model
#   result, texts = model.eval_model(eval_data)
#   wandb.join()

In [ ]:
# wandb.agent(sweep_id, train)


INFO:wandb.agents.pyagent:Starting sweep agent: entity=None, project=None, count=None
wandb: Agent Starting Run: asw2knye with config:
wandb: 	learning_rate: 0.0002735151893788527
wandb: 	max_seq_length: 128
wandb: 	num_train_epochs: 5
wandb: 	train_batch_size: 16
wandb: Currently logged in as: billu (use `wandb login --relogin` to force relogin)


Downloading:   0%|          | 0.00/491 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/424M [00:00<?, ?B/s]

Some weights of the model checkpoint at asafaya/bert-base-arabic were not used when initializing BertForQuestionAnswering: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForQuestionAnswering from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForQuestionAnswering from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForQuestionAnswering were not initialized from the model checkpoint at asafaya/bert-base-arabic and are newly i

Downloading:   0%|          | 0.00/326k [00:00<?, ?B/s]

...

Running Evaluation:   0%|          | 0/14 [00:00<?, ?it/s]

Running Epoch 1 of 5:   0%|          | 0/23 [00:00<?, ?it/s]

INFO:simpletransformers.question_answering.question_answering_model: Converting to features started.

convert squad examples to features: 100%|██████████| 109/109 [00:00<00:00, 160.85it/s]

add example index and unique id: 100%|██████████| 109/109 [00:00<00:00, 278258.76it/s]


Running Evaluation:   0%|          | 0/14 [00:00<?, ?it/s]

Running Epoch 2 of 5:   0%|          | 0/23 [00:00<?, ?it/s]

In [ ]:
model = QuestionAnsweringModel(
    "bert", "asafaya/bert-base-arabic", args=model_args
)
# Train the model
model.train_model(train_data, eval_data=eval_data,output_dir='tillu')

# Evaluate the model
result, texts = model.eval_model(eval_data)

Some weights of the model checkpoint at asafaya/bert-base-arabic were not used when initializing BertForQuestionAnswering: ['cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight']
- This IS expected if you are initializing BertForQuestionAnswering from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForQuestionAnswering from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForQuestionAnswering were not initialized from the model checkpoint at asafaya/bert-base-arabic and are newly i

Epoch:   0%|          | 0/5 [00:00<?, ?it/s]

Running Epoch 0 of 5:   0%|          | 0/45 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/torch/optim/lr_scheduler.py:134: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  "https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate", UserWarning)
INFO:simpletransformers.question_answering.question_answering_model: Converting to features started.

convert squad examples to features: 100%|██████████| 109/109 [00:00<00:00, 210.74it/s]

add example index and unique id: 100%|██████████| 109/109 [00:00<00:00, 352218.13it/s]


Running Evaluation:   0%|          | 0/14 [00:00<?, ?it/s]

...

Running Epoch 4 of 5:   0%|          | 0/45 [00:00<?, ?it/s]

INFO:simpletransformers.question_answering.question_answering_model: Converting to features started.

convert squad examples to features: 100%|██████████| 109/109 [00:00<00:00, 225.38it/s]

add example index and unique id: 100%|██████████| 109/109 [00:00<00:00, 341688.44it/s]


Running Evaluation:   0%|          | 0/14 [00:00<?, ?it/s]

INFO:simpletransformers.question_answering.question_answering_model: Training of bert model complete. Saved to tillu.
INFO:simpletransformers.question_answering.question_answering_model: Converting to features started.
add example index and unique id: 100%|██████████| 109/109 [00:00<00:00, 473760.76it/s]


Running Evaluation:   0%|          | 0/14 [00:00<?, ?it/s]

In [ ]:
result


{'correct': 12,
 'similar': 81,
 'incorrect': 16,
 'eval_loss': -5.127790178571429}

In [ ]:
result


{'correct': 10,
 'similar': 88,
 'incorrect': 11,
 'eval_loss': -5.870256696428571}

In [ ]:
result


{'correct': 15,
 'similar': 53,
 'incorrect': 41,
 'eval_loss': -6.368861607142857}

In [ ]:
test = pd.read_json("/content/quranqa/datasets/qrcd_v1.1_test_noAnswers.jsonl",lines = True)

In [ ]:
test.head()

pq_id                                            passage  surah  \
0   31:12-19_135  ولقد آتينا لقمان الحكمة أن اشكر لله ومن يشكر ف...     31   
1  2:234-237_124  والذين يتوفون منكم ويذرون أزواجا يتربصن بأنفسه...      2   
2    2:87-88_241  ولقد آتينا موسى الكتاب وقفينا من بعده بالرسل و...      2   
3   2:97-101_241  قل من كان عدوا لجبريل فإنه نزله على قلبك بإذن ...      2   
4  2:102-103_241  واتبعوا ما تتلو الشياطين على ملك سليمان وما كف...      2   

    verses                             question answers  
0    12-19             ما هي وصايا لقمان لابنه؟      []  
1  234-237                  كم مدة عدة الأرملة؟      []  
2    87-88  من هم الملائكة المذكورون في القرآن؟      []  
3   97-101  من هم الملائكة المذكورون في القرآن؟      []  
4  102-103  من هم الملائكة المذكورون في القرآن؟      []

In [ ]:
# test['answers'] = test['answers'].apply(lambda x:chnager(x))

In [ ]:
final_dict_test = list()
for id, contxt,qn in zip(test.pq_id.values,test.passage.values,test.question.values):
  ele_dict = dict()
  ele_dict['context'] = contxt
  l = []
  dd = {"id":id,"is_impossible": False,"question":qn}
  l.append(dd)
  ele_dict['qas'] = l
  final_dict_test.append(ele_dict)

In [ ]:
to_predict = final_dict_test

In [ ]:
answers, probabilities = model.predict(to_predict)


INFO:simpletransformers.question_answering.question_answering_model: Converting to features started.
add example index and unique id: 100%|██████████| 274/274 [00:00<00:00, 522144.16it/s]


Running Prediction:   0%|          | 0/35 [00:00<?, ?it/s]

In [ ]:
case_list = {}
for anss,probs in zip(answers,probabilities):
  id = anss['id']
  ans_list = []
  # cl={}
  i = 1
  for ans,prob in zip(anss['answer'],probs['probability']):
    ans_list.append({"answer":ans,"rank":i,"score":prob})
    i = i+1
  case_list[id] = ans_list



In [ ]:
case_list = {}
for anss,probs in zip(answers,probabilities):
  id = anss['id']
  ans_list = []
  # cl={}
  i = 1
  for ans,prob in zip(anss['answer'],probs['probability']):
    if i == 6:
      break
    else:
      ans_list.append({"answer":ans,"rank":i,"score":prob})
      i = i+1
  case_list[id] = ans_list



In [ ]:
case_list

{'31:12-19_135': [{'answer': 'ومن يشكر فإنما يشكر لنفسه ومن كفر فإن الله غني حميد.',
   'rank': 1,
   'score': 0.8718261633022506},
  {'answer': 'ولقد آتينا لقمان الحكمة أن اشكر لله ومن يشكر فإنما يشكر لنفسه ومن كفر فإن الله غني حميد.',
   'rank': 2,
   'score': 0.03806298904171385},
  {'answer': 'ومن يشكر فإنما يشكر لنفسه ومن كفر فإن الله غني حميد. وإذ قال لقمان لابنه وهو يعظه يا بني لا تشرك بالله إن الشرك لظلم عظيم.',
   'rank': 3,
   'score': 0.018981059480687575},
  {'answer': 'ومن يشكر فإنما يشكر لنفسه ومن كفر فإن الله غني حميد. وإذ قال لقمان لابنه وهو يعظه يا بني لا تشرك بالله إن الشرك لظلم',
   'rank': 4,
   'score': 0.018962532337717396},
  {'answer': 'ومن يشكر فإنما يشكر لنفسه ومن كفر فإن الله غني حميد. وإذ قال لقمان لابنه وهو يعظه يا بني لا تشرك بالله إن الشرك لظلم عظيم. ووصينا الإنسان بوالديه حملته أمه',
   'rank': 5,
   'score': 0.018962532337717396}],
 '2:234-237_124': [{'answer': 'والذين يتوفون منكم ويذرون أزواجا يتربصن بأنفسهن أربعة أشهر وعشرا فإذا بلغن أجلهن فلا جناح عل

In [ ]:
import json 
with open("niksss_run01.json", "w") as outfile:
    json.dump(case_list, outfile)

In [ ]:
case_list.to_json('submission.jsonl',orient='records',lines=True)

AttributeError: ignored